# Importing ORACC Data from corpus.json
by Niek Veldhuis
UC Berkeley

February 2017

# TODO
* check that COFs are treated properly
* check that lines that continue into the next line (as in bilinguals) are captured completely.


# Introduction

Purpose of the code is to download [ORACC](http://oracc.org) JSON files that contain textual data and produce a `.csv` file with the relevant data for use in computational text analysis. This comes in the place of scraping the published `html` (see the [Scrape-ORACC](https://github.com/niekveldhuis/Digital-Assyriology/tree/master/Scrape-Oracc) repo). The JSON files contain all the transliteration and lemmatization data of an ORACC project (metadata are made available in a separate `.json` file). For an introduction to the various ORACC JSON files see the [ORACC Open Data](http://oracc.org/doc/opendata) page.

The resulting data file may include various elements of the ORACC data structure. The current code will output a file with the following fields: 

* id_text 
* lemma (listing all the lemmas of that text in sequence)

The selection and arrangement of fields may be adjusted with standard `Pandas` functions.

## Notes
The current version of the script works with the `ijson` library. Documentation for [ijson](https://www.dataquest.io/blog/python-json-tutorial/), unfortunately, is extremely brief. The notebook has been tested, using a list of 106 P, Q, X numbers (in `ob_lists_wood.txt`). Downloading the `.json` files from the ORACC server takes between 30 and 45 seconds. The rest of the script is reasonably fast. With larger lists of text IDs the script will obviously take longer. 

This notebook is written for **Python 3.5** with **Pandas 0.19** and **ijson 2.3**.

The notebook was originally written for the [Phylogenetics](https://github.com/ErinBecker/digital-humanities-phylogenetics) project with Erin Becker of [Data Carpentry](http://www.datacarpentry.org). The particular data selection and data manipulation performed in this notebook are adapted for use in the word2vec project. It should be fairly easy to adapt the notebook to the purposes of any other project that wishes to use [ORACC](http://oracc.org) data.

## Licensing
This notebook may be downloaded, used and adapted without any restrictions.

In [1]:
import pandas as pd   
import ijson
import urllib.request
import re
import tqdm
import numpy as np

# Input List of Text IDs or a project abbreviation
Identify a list of text IDs (P, Q, and X numbers) in the directory `input`. The IDs are six-digit P, Q, or X numbers preceded by a project abbreviation in the format 'PROJECT/P######' or 'PROJECT/SUBPROJECT/Q######'. For example:
* dcclt/P117395
* etcsri/Q001203
* rinap/rinap1/Q003421

The list should be created with a flat text editor such as Textedit or Emacs, and the filename should end in `.txt`.

Alternatively, one may enter the name (abbreviation) of a project or sub-project in [ORACC](http://oracc.org) and pull all the lemmatized data from that project. Note that the script will not automatically pull data from subprojects, they have to be requested separately. Examples:
* saao/saa01
* aemw/amarna
* rimanum

In [2]:
name = input('Filename or project abbreviation: ')

Filename or project abbreviation: hbtin


In [3]:
if name[-4:] == '.txt':
    textids = 'text_ids/' + name
    with open(textids, 'r') as f:
        pqxnos = f.readlines()
    pqxnos = [x.strip() for x in pqxnos]
    files = [x[:-7] + 'corpusjson/' + x[-7:] + '.json' for x in pqxnos]
    pqxnos = [x[-7:] for x in pqxnos]
    pqxnos[:5], files[:5]
else:
    files = []
    json = '/metadata.json'
    url = 'http://oracc.museum.upenn.edu/' + name + json
    try:
        d = urllib.request.urlopen(url)
        parser = ijson.parse(d)
        for prefix, event, value in parser:
            #print(prefix)
            if prefix == 'formats.lem.item':   # get only lemmatized texts
                files.append(name + '/corpusjson/' + value + '.json')
    except:
        print(url + ' not available')

# Parse
The function `oraccjasonparser()` takes one argument (the **url** of the `.json` file). It looks for the prefix `textid` to retrieve the six-digit P, Q, or X number of the text artifact. Parsing the file sequentially the code looks for the places where a line starts (`'.type' = 'line-start'`) and where a word starts (`'.node' = 'l'`, where `l` is for "lemma"). At each level the code will retrieve the relevant data and create a list where each entry is a dictionary that represents a single word. 

Words not only include lemmatized words, but also unlemmatized and unlemmatizable words (such as breaks).

The dictionary includes the keys `id_line` and `id_word` that allow the user to reassemble words and lines in order.

In [27]:
def oraccjsonparser(url):
    d = urllib.request.urlopen(url)
    parser = ijson.parse(d)
    word_l = []
    word_d = {}
    line_start = False
    word_start = False
    nonx = False
    for prefix, event, value in parser:
        if prefix == 'textid':
            id_text = value
#            print("parsing " + value)
        if prefix.endswith('.type'):
            if value == 'line-start':
                line_start = True
            else:
                line_start = False
        if line_start:
            if prefix.endswith('.ref') and not word_start:
                id_line = value # id_line is a reference number for a line
                                # that includes the id_text (e.g. P123456.49)
            if prefix.endswith('.label'):
                label = value   # label is a human-readable line number of the format
                                # o ii 24' (obverse column 2 line 24')
        if prefix.endswith('node'):
            if value == 'l':
                #print(prefix)
                word_start = True
                if not word_d == {}:
                    word_l.append(word_d) # append the previous word to the list
                word_d = {}               # and start a new dictionary
                #word_d['id_text'] = id_text # provide each word with appropriate 
                #word_d['id_line'] = id_line # text and line-ID
                word_d['label'] = label     # and the line label.
            else:
                word_start = False
        if word_start:
            if prefix.endswith('cdl.item.ref') or prefix.endswith('choices.item.ref'):
                #print(prefix), print(value)
                word_d['id_word'] = value
                id_elements = value.split('.')
                word_d['id_text'] = id_elements[0]
                word_d['id_line'] = id_elements[0] + '.' + id_elements[1]
            if prefix.endswith('.sig'):
                word_d['signature'] = value
            if '.f.' in prefix:
                category = re.sub('.*\.', '', prefix) # get element after the last dot of the prefix
                word_d[category] = value # copy each element into the dictionary
        if prefix.endswith('.type'):
            if value == 'nonx':
                nonx = True
            else:
                nonx = False
        if nonx:                         # this captures so-called $-lines with information
            if prefix.endswith('.ref'):  # about number of broken lines/columns.
                id_line = value          # $-lines have their own id_line.
            if prefix.endswith('.strict'):
                if value == '1':           # select only 'strict' $ lines
                    if not word_d == {}:
                        word_l.append(word_d)
                    word_d = {}
                    word_d['id_line'] = id_line
                    word_d['id_text'] = id_text
                else:
                    nonx = False
            if prefix.endswith('.extent'): # capture the three elements of strict $ lines
                word_d['extent'] = value   # namely extent, scope, and state.
            if prefix.endswith('.scope'):
                word_d['scope'] = value
            if prefix.endswith('.state'):
                word_d['state'] = value

    word_l.append(word_d)  # make sure that the last word is captured, too.
    return(word_l) # return a list of dictionaries, where each entry (dictionary) in
                   # the list represents a word.

# Call the Parser Function for Each Textid

In [5]:
url_prefix = "http://oracc.museum.upenn.edu/"
word_l = []
for id_text in tqdm.tqdm(files):   # tqdm creates a progress bar
    try:
        url = url_prefix + id_text
        word_l.extend(oraccjsonparser(url))
    except:
        print(url + ' not available') 

  0%|          | 0/451 [00:00<?, ?it/s]

cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.ref
P235192.3.1
cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.ref
P235192.3.2
cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.ref
P235192.3.3
cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.ref
P235192.3.4
cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.ref
P235192.3.5
cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.ref
P235192.3.6
cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.ref
P235192.3.7
cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.ref
P235192.3.8
cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.ref
P235192.3.9
cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.ref
P235192.3.10
cdl.item.cdl.item.cdl.item.cdl.item.ref
P235192.3.11
cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.ref
P235192.4.1
cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.ref
P235192.4.2
cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.ref
P235192.4.3
cdl.item.cdl.item.cdl.item.cdl.item.ref
P235192.4.4
cdl.item.cdl.item.cdl.item.cdl.item.ref
P235192.4.5
cdl.item.cdl.

  0%|          | 1/451 [00:01<09:19,  1.24s/it]

cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.ref
P235192.67.1
cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.ref
P235192.70.1
cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.ref
P235192.72.1
cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.ref
P235192.74.1
cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.ref
P235192.76.1
cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.ref
P235192.78.1
cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.ref
P235192.80.1
cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.ref
P235192.82.1
cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.ref
P235192.84.1
cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.ref
P235192.86.1
cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.ref
P235192.88.1
cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.ref
P235192.91.1
cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.ref
P235192.91.2
cdl.item.cdl.item.cdl.item.cdl.item.ref
P296411.3.1
cdl.item.cdl.item.cdl.item.cdl.item.ref
P296411.3.2
cdl.item.cdl.item.cdl.item.

  0%|          | 2/451 [00:02<09:36,  1.28s/it]

...

100%|█████████▉| 449/451 [07:46<00:02,  1.21s/it]

cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.ref
P388068.3.1
cdl.item.cdl.item.cdl.item.cdl.item.ref
P388068.3.2
cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.ref
P388068.3.3
cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.ref
P388068.3.4
cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.ref
P388068.3.5
cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.ref
P388068.3.6
cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.ref
P388068.3.7
cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.ref
P388068.3.8
cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.ref
P388068.4.1
cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.ref
P388068.4.2
cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.ref
P388068.4.3
cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.ref
P388068.4.4
cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.ref
P388068.4.5
cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.ref
P388068.4.6
cdl.item.cdl.item.cdl.item.cdl.item.ref
P388068.4.7
cdl.item.cdl.item.cdl.item.cdl.item.ref
P388068.4.8
cdl.item.cdl.it

100%|█████████▉| 450/451 [07:48<00:01,  1.39s/it]

cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.ref
P388069.3.1
cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.ref
P388069.3.2
cdl.item.cdl.item.cdl.item.cdl.item.ref
P388069.3.3
cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.ref
P388069.3.4
cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.ref
P388069.3.5
cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.ref
P388069.3.6
cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.ref
P388069.3.7
cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.ref
P388069.3.8
cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.ref
P388069.3.9
cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.ref
P388069.3.10
cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.ref
P388069.3.11
cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.ref
P388069.3.12
cdl.item.cdl.item.cdl.item.cdl.item.ref
P388069.3.13
cdl.item.cdl.item.cdl.item.cdl.item.ref
P388069.4.1
cdl.item.cdl.item.cdl.item.cdl.item.ref
P388069.4.2
cdl.item.cdl.item.cdl.item.cdl.item.ref
P388069.4.3
cdl.item.cdl.item.cdl.item.cdl.item.re

100%|██████████| 451/451 [07:49<00:00,  1.32s/it]


# Transform the Data into a DataFrame

In [6]:
words = pd.DataFrame(word_l)
words.head()
#words.loc[words['id_text'] == 'P357082']

cf epos extent                  form   gw    id_line  id_text  \
0  Anu-ah-ittannu   PN    NaN  {m}{d}60-ŠEŠ-MU{+nu}   00  P235192.3  P235192   
1            māru    N    NaN                  DUMU  son  P235192.3  P235192   
2              ša  DET    NaN                   ša₂   of  P235192.3  P235192   
3     Nidintu-Anu   PN    NaN   {m}ni-din-tu₄-{d}60   00  P235192.3  P235192   
4            māru    N    NaN                  DUMU  son  P235192.3  P235192   

       id_word label          lang            norm  pos scope sense  \
0  P235192.3.1   o 1  akk-x-ltebab  Anu-ah-ittannu   PN   NaN    00   
1  P235192.3.2   o 1  akk-x-ltebab            māru    N   NaN   son   
2  P235192.3.3   o 1  akk-x-ltebab              ša  DET   NaN    of   
3  P235192.3.4   o 1  akk-x-ltebab     Nidintu-Anu   PN   NaN    00   
4  P235192.3.5   o 1  akk-x-ltebab            māri    N   NaN   son   

                                           signature state  
0  @hbtin%akk-x-ltebab:{m}{d}60-ŠEŠ-MU{+nu}=Anu-a...   NaN  
1    @hbtin%akk-x-ltebab:DUMU=māru[son//son]N'N$māru   NaN  
2       @hbtin%akk-x-ltebab:ša₂=ša[of//of]DET'DET$ša   NaN  
3  @hbtin%akk-x-ltebab:{m}ni-din-tu₄-{d}60=Nidint...   NaN  
4    @hbtin%akk-x-ltebab:DUMU=māru[son//son]N'N$māri   NaN

# Remove Spaces and Commas from Guide Word and Sence
Spaces in Guide Word and Sense may cause trouble in computational methods in tokenization, or when saved in Comma Separated Values format. All spaces and commas are replaced by hyphens or nothing, respectively.

In [7]:
words = words.fillna('') # first replace Missing Values by empty string
words['sense'] = [x.replace(' ', '-') for x in words['sense']]
words['sense'] = [x.replace(',', '') for x in words['sense']]
words['gw'] = [x.replace(' ', '-') for x in words['gw']]
words['gw'] = [x.replace(',', '') for x in words['gw']]

The columns in the resulting DataFrame correspond to the elements of a full [ORACC](http://oracc.org) signature, plus information about text, line, and word ids:
* base (Sumerian only)
* cf (Citation Form)
* cont (continuation of the base; Sumerian only)
* epos (Effective Part of Speech)
* form (transliteration, omitting all flags such as indication of breakage)
* gw (Guide Word: main or first translation in standard dictionary)
* id_line (a line ID that begins with the six-digit P, Q, or X number of the text)
* id_text (six-digit P, Q, or X number)
* id_word (word ID that begins with the ID number of the line)
* label (traditional line number in the form o ii 2' (obverse column 2 line 2'), etc.)
* lang (language code, including sux, sux-x-emegir, sux-x-emesal, akk, akk-x-stdbab, etc)
* morph (Morphology; Sumerian only)
* norm (Normalization: Akkadian)
* norm0 (Normalization: Sumerian)
* pos (Part of Speech)
* sense (contextual meaning)
* signature (full ORACC signature)

Not all data elements (columns) are available for all words. Sumerian words never have a `norm`, Akkadian words do not have `norm0`, `base`, `cont`, or `morph`. Most data elements are only present when the word is lemmatized; only `lang`, `form`, `pos`, `id_word`, `id_line`, and `id_text` should always be there. An unlemmatized word has `pos` 'X' (for unknown). Broken words have `pos` 'u' (for 'unlemmatizable).

# Manipulate
The columns may be manipulated with standard Pandas methods to create the desired output. By way of example, the following code will create a column `lemma` with the format **cf[gw]pos** (for instance **lugal[king]N**). For words that have no lemmatization `lemma` equals `form`. Only Sumerian words are allowed (and thus `lang` can be omitted) and in addition to the column `lemma` the column `base` is preserved; words that have no lemmatization take `form` as their base. Words and bases are concatenated to lines.

## Remove  non-Akkadian words

In [8]:
lang = ['akk', ''] # note that 'lang' is empty in entries that indicate damage
words = words.loc[words['lang'].str[:3].isin(lang)].reset_index()

## Create Lemma Column and Adjust Base

In [9]:
words['lemma'] = words['cf'] # first element of lemma is the citation form
words['lemma'] = [words['lemma'][i] + '[' + words['gw'][i] + ']' + words['pos'][i] 
                  if not words['lemma'][i] == '' 
                  else words['form'][i] +'[NA]NA' for i in range(len(words))]
words['lemma'] = [lemma if not lemma == '[NA]NA' else '' for lemma in words['lemma'] ]
#words['base'] = [words['base'][i] if not words['base'][i] == '' 
#                 or words['label'][i] == '' else words['form'][i] 
#                 for i in range(len(words))]
lemmas = words[['lemma', 'id_text', 'id_line', 'id_word', 'label']]#, 'extent', 'scope']]
#lemmas = words[['lemma', 'base', 'id_text', 'id_line', 'id_word', 'label', 'extent', 'scope']]
lemmas.head()

lemma  id_text    id_line      id_word label
0  Anu-ah-ittannu[00]PN  P235192  P235192.3  P235192.3.1   o 1
1            māru[son]N  P235192  P235192.3  P235192.3.2   o 1
2             ša[of]DET  P235192  P235192.3  P235192.3.3   o 1
3     Nidintu-Anu[00]PN  P235192  P235192.3  P235192.3.4   o 1
4            māru[son]N  P235192  P235192.3  P235192.3.5   o 1

In [19]:
lemmas[lemmas['lemma'] == 'u[and]CNJ'][lemmas['id_line']=='']

//anaconda/lib/python3.5/site-packages/ipykernel/__main__.py:1: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  if __name__ == '__main__':


lemma id_text id_line id_word label
27412  u[and]CNJ                           o 9
27413  u[and]CNJ                           o 9

## Group by Line

In [20]:
lemmas[27410:27420]

lemma  id_text     id_line       id_word label
27410      Rahmat-Anu[00]PN  P296769  P296769.11  P296769.11.3   o 9
27411        Atalihan[00]PN  P296769  P296769.11  P296769.11.4   o 9
27412             u[and]CNJ                                      o 9
27413             u[and]CNJ                                      o 9
27414   Anu-ah-tuqqin[00]PN  P296769  P296769.11  P296769.11.6   o 9
27415         wardu[slave]N  P296769  P296769.12  P296769.12.1  o 10
27416        šunūti[them]IP  P296769  P296769.12  P296769.12.2  o 10
27417          bašû[exist]V  P296769  P296769.12  P296769.12.3  o 10
27418  Mannu-ki-Ištar[00]PN  P296769  P296769.12  P296769.12.4  o 10
27419          marāqu[rub]V  P296769  P296769.12  P296769.12.5  o 10

In [10]:
lines = words.groupby([words['id_line'], words['label']]).agg({
        'lemma': ' '.join,
        #'base': ' '.join,
        #'extent': ''.join, 
        #'scope': ''.join
    }).reset_index()
        

In [11]:
df = lines[['id_line', 'label', 'lemma']] #, 'base', 'extent', 'scope']]

In [15]:
df['id_text'] = df['id_line'].str[:7] # id_text was lost in the grouping above and is recreated
df['line'] = [re.sub('.+\.', '', line) for line in df['id_line']] #create a line number for sorting
df['line'] = [x.replace('l', '') for x in df['line']]
df

id_line       label  \
0                         o 9   
1      P235192.10         o 8   
2      P235192.11         o 9   
3      P235192.12        o 10   
4      P235192.13        o 11   
5      P235192.14        o 12   
6      P235192.15        o 13   
7      P235192.16        o 14   
8      P235192.17        o 15   
9      P235192.19         r 1   
10     P235192.20         r 2   
11     P235192.21         r 3   
12     P235192.22         r 4   
13     P235192.23         r 5   
14     P235192.24         r 6   
15     P235192.25         r 7   
16     P235192.26         r 8   
17     P235192.27         r 9   
18     P235192.28        r 10   
19     P235192.29        r 11   
20      P235192.3         o 1   
21     P235192.30        r 12   
22     P235192.31        r 13   
23     P235192.32        r 14   
24     P235192.33        r 15   
25     P235192.36    t.e. i 1   
26     P235192.38    t.e. i 2   
27      P235192.4         o 2   
28     P235192.40   t.e. ii 1   
29     P235192.42   t.e. ii 2   
...           ...         ...   
21948   P388069.4         o 2   
21949  P388069.41               
21950  P388069.43   t.e. ii 1   
21951  P388069.44               
21952  P388069.45   t.e. ii 2   
21953  P388069.47  t.e. iii 1   
21954  P388069.49  t.e. iii 2   
21955   P388069.5         o 3   
21956  P388069.51   t.e. iv 1   
21957  P388069.53   t.e. iv 2   
21958  P388069.55    t.e. v 1   
21959  P388069.56               
21960  P388069.57    t.e. v 2   
21961  P388069.59               
21962   P388069.6         o 4   
21963  P388069.62    l.e. i 1   
21964  P388069.63               
21965  P388069.64    l.e. i 2   
21966  P388069.66   l.e. ii 1   
21967  P388069.67               
21968  P388069.68   l.e. ii 2   
21969   P388069.7         o 5   
21970  P388069.72    r.e. i 1   
21971  P388069.74    r.e. i 2   
21972  P388069.76   r.e. ii 1   
21973  P388069.78   r.e. ii 2   
21974   P388069.8         o 6   
21975  P388069.80  r.e. iii 1   
21976  P388069.82  r.e. iii 2   
21977   P388069.9         o 7   

                                                   lemma  id_text line  
0                                    u[and]CNJ u[and]CNJ                
1      istatirru[stater]N ša[of]DET Seleucus[1]RN bab...  P235192   10  
2      ana[to]PRP Kidin-Anu[00]PN māru[son]N ša[of]DE...  P235192   11  
3      ana[to]PRP ūmu[day]N ṣiātu[distant-time]N nadā...  P235192   12  
4      šuāti[him]IP Anu-ah-ittannu[00]PN ina[in]PRP q...  P235192   13  
5      ana[to]PRP muhhu[skull]N mišlu[half]NU ūmu[day...  P235192   14  
6      bašû[exist]V Anu-ah-ittannu[00]PN nādinu[giver...  P235192   15  
7      marāqu[rub]V adi[until]PRP 12-TA.AM₃[NA]NA ana...  P235192   16  
8      nadānu[give]V mišlu[half]NU ūmu[day]N ina[in]P...  P235192   17  
9      ūmu[day]N 29-KAM₂[NA]NA ūmu[day]N 30-KAM₂[NA]N...  P235192   19  
10     Anu-ahhe-iddin[00]PN māru[son]N ša[of]DET Nana...  P235192   20  
11     ūmu[day]N mala[as-much-as]PRP Kidin-Anu[00]PN ...  P235192   21  
12     ša[that]REL ina[in]PRP bītu[house]N ilu[god]N ...  P235192   22  
13                                     mukinnu[witness]N  P235192   23  
14     Anu-mukin-apli[00]PN māru[son]N ša[of]DET Anu-...  P235192   24  
15     Anu-ah-ittannu[00]PN māru[son]N ša[of]DET Ana-...  P235192   25  
16     māru[son]N ša[of]DET Kidin-Anu[00]PN māru[son]...  P235192   26  
17     Anu-ab-uṣur[00]PN māru[son]N ša[of]DET Nanaya-...  P235192   27  
18     Balaṭu[00]PN māru[son]N ša[of]DET Anu-ahhe-idd...  P235192   28  
19     Labaši[00]PN māru[son]N Ekur-zakir[1]LN Ina-qi...  P235192   29  
20     Anu-ah-ittannu[00]PN māru[son]N ša[of]DET Nidi...  P235192    3  
21     māru[son]N ša[of]DET Ana-rabut-Anu[00]PN māru[...  P235192   30  
22     Anu-ah-iddin[00]PN māru[son]N ša[of]DET Šamaš-...  P235192   31  
23     Dumqi-Anu[00]PN ṭupšarru[scribe]N māru[son]N š...  P235192   32  
24     ūmu[day]N 7-KAM₂[NA]NA šattu[year]N 80-KAM₂[NA...  P235192   33  
25                                           unqu[ring]N  P235192

In [14]:
df['line'] = [int(x) for x in df['line']]
df = df.sort_values(['id_text', 'line']).reset_index(drop=True)
df.head(100)

ValueError: invalid literal for int() with base 10: ''

In [ ]:
df = df.loc[np.where(df['lemma'] != '')] # kick out rows with empty lemma field
df

In [ ]:
grouped = df['lemma'].groupby(df['id_text']).apply(' '.join).reset_index()
by_text_df = pd.DataFrame(grouped)
by_text_df = by_text_df.set_index('id_text')
by_text_df

## Save in CSV Format

In [ ]:
if name[-4:] == '.txt': # list of P/Q/X numbers in .txt file
    filename = name[:-4]
else:                  # full project
    filename = name.replace('/', '_')
with open('output/' + filename + '.csv', 'w') as w:
    by_text_df.to_csv(w, encoding='utf8')

In [26]:
oraccjsonparser('http://oracc.museum.upenn.edu/hbtin/corpusjson/P296769.json')

cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.ref
P296769.3.1
cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.ref
P296769.3.2
cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.ref
P296769.3.3
cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.ref
P296769.3.4
cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.ref
P296769.3.5
cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.ref
P296769.3.6
cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.ref
P296769.3.7
cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.ref
P296769.3.8
cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.ref
P296769.3.9
cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.ref
P296769.4.1
cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.ref
P296769.4.2
cdl.item.cdl.item.cdl.item.cdl.item.cdl.item.ref
P296769.4.3
cdl.item.cdl.item.cdl.item.cdl.item.ref
P296769.4.4
cdl.item.cdl.item.cdl.item.cdl.item.ref
P296769.4.5
cdl.item.cdl.item.cdl.item.cdl.item.ref
P296769.4.6
cdl.item.cdl.item.cdl.item.cdl.item.ref
P296769.4.7
cdl.item.cdl.it

[{'cf': 'Mannu-ki-Ištar',
  'epos': 'PN',
  'form': '{m}man-nu-ki-i-{d}DIL-BAT',
  'gw': '00',
  'id_line': 'P296769.3',
  'id_text': 'P296769',
  'id_word': 'P296769.3.1',
  'label': 'o 1',
  'lang': 'akk-x-ltebab',
  'norm': 'Mannu-ki-Ištar',
  'pos': 'PN',
  'sense': '00',
  'signature': "@hbtin%akk-x-ltebab:{m}man-nu-ki-i-{d}DIL-BAT=Mannu-ki-Ištar[00//00]PN'PN$Mannu-ki-Ištar"},
 {'cf': 'māru',
  'epos': 'N',
  'form': 'DUMU',
  'gw': 'son',
  'id_line': 'P296769.3',
  'id_text': 'P296769',
  'id_word': 'P296769.3.2',
  'label': 'o 1',
  'lang': 'akk-x-ltebab',
  'norm': 'māru',
  'pos': 'N',
  'sense': 'son',
  'signature': "@hbtin%akk-x-ltebab:DUMU=māru[son//son]N'N$māru"},
 {'cf': 'ša',
  'epos': 'DET',
  'form': 'ša₂',
  'gw': 'of',
  'id_line': 'P296769.3',
  'id_text': 'P296769',
  'id_word': 'P296769.3.3',
  'label': 'o 1',
  'lang': 'akk-x-ltebab',
  'norm': 'ša',
  'pos': 'DET',
  'sense': 'of',
  'signature': "@hbtin%akk-x-ltebab:ša₂=ša[of//of]DET'DET$ša"},
 {'cf': 'Anu-ah